<a href="https://colab.research.google.com/github/JunLiang1214/222726Y/blob/master/sentiment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [4]:
from mpl_toolkits.mplot3d import Axes3D
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import tensorflow as tf
from tensorflow.keras import Input, Model
from sklearn import preprocessing


In [5]:
with open("train.ft.txt", "r", encoding="utf-8") as trainingData:
    df = pd.DataFrame({"Text": trainingData.readlines()})

with open("test.ft.txt", "r", encoding="utf-8") as testingData:
    df_Test = pd.DataFrame({"Text": testingData.readlines()})
#training data set [3600000 rows x 1 columns]
df[['Label', 'Text']] = df['Text'].str.split(n=1, expand=True)
df_Test[['Label', 'Text']] = df['Text'].str.split(n=1, expand=True)
X_train,y_train = df['Text'],df['Label']
X_test,y_test = df['Text'],df['Label']

In [6]:
y_train_array = np.array(y_train)
if isinstance(y_train_array, tf.Tensor):
    y_train_array = y_train_array.numpy()
mlb = preprocessing.MultiLabelBinarizer()

y_train= mlb.fit_transform(y_train_array)
y_train = y_train[:,0]


In [7]:

token = tf.keras.preprocessing.text.Tokenizer(num_words=20000)
token.fit_on_texts(X_train)

# print(X_train)
np.shape(X_train)
token.get_config()

{'num_words': 20000,
 'filters': '!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
 'lower': True,
 'split': ' ',
 'char_level': False,
 'oov_token': None,
 'document_count': 27977,
 'word_counts': '{"stuning": 1, "even": 4077, "for": 23161, "the": 113482, "non": 424, "gamer": 6, "this": 43246, "sound": 1251, "track": 499, "was": 20306, "beautiful": 740, "it": 44903, "paints": 19, "senery": 2, "in": 27217, "your": 4715, "mind": 663, "so": 9255, "well": 4283, "i": 59220, "would": 6514, "recomend": 121, "to": 53510, "people": 2497, "who": 4568, "hate": 384, "vid": 4, "game": 1294, "music": 2436, "have": 14265, "played": 452, "chrono": 7, "cross": 92, "but": 16674, "out": 6297, "of": 47538, "all": 9448, "games": 298, "ever": 2658, "has": 6243, "best": 3532, "backs": 11, "away": 1040, "from": 7206, "crude": 37, "keyboarding": 1, "and": 61182, "takes": 606, "a": 57570, "fresher": 7, "step": 178, "with": 15756, "grate": 8, "guitars": 46, "soulful": 34, "orchestras": 3, "impress": 34, "anyone": 1471, "

In [14]:
X_test = token.texts_to_sequences(X_test)

AttributeError: 'int' object has no attribute 'lower'

In [15]:

# Convert text sequences to integer sequences (tokenization)
# X_train_seq = token.texts_to_sequences(X_train)

# Pad sequences to ensure uniform length
X_train = token.texts_to_sequences(X_train)
max_seq_length = 50  # or any other desired sequence length
X_train = tf.keras.preprocessing.sequence.pad_sequences(X_train, maxlen=max_seq_length, padding="pre", truncating="post")
X_train.shape



(27977, 50)

In [17]:
v = len(token.word_index)

In [18]:
#input for embedding must be the total vocab size + 1
inputs = Input(shape = X_train[0].shape)
x = tf.keras.layers.Embedding(v+1,60)(inputs)
x1 = tf.keras.layers.SimpleRNN(128)(x)
x2 = tf.keras.layers.Flatten()(x1)
x3 = tf.keras.layers.Dense(128,activation="relu")(x2)
x4=tf.keras.layers.Dense(units=1,activation="sigmoid")(x3)
model = Model(inputs=inputs, outputs=x4)

In [ ]:
type(X_train)

numpy.ndarray

In [23]:
model.compile(optimizer="adam",loss="binary_crossentropy",metrics=["accuracy"])

model.fit(X_train,y_train,epochs=20)

Epoch 1/20
875/875 [==============================] - 69s 76ms/step - loss: 0.5363 - accuracy: 0.7369
Epoch 2/20
875/875 [==============================] - 65s 74ms/step - loss: 0.4838 - accuracy: 0.7722
Epoch 3/20
875/875 [==============================] - 65s 74ms/step - loss: 0.4607 - accuracy: 0.7912
Epoch 4/20
875/875 [==============================] - 65s 74ms/step - loss: 0.4581 - accuracy: 0.7935
Epoch 5/20
875/875 [==============================] - 65s 75ms/step - loss: 0.4465 - accuracy: 0.8013
Epoch 6/20
875/875 [==============================] - 66s 75ms/step - loss: 0.3764 - accuracy: 0.8391
Epoch 7/20
875/875 [==============================] - 65s 75ms/step - loss: 0.3141 - accuracy: 0.8744
Epoch 8/20
875/875 [==============================] - 65s 74ms/step - loss: 0.3931 - accuracy: 0.8267
Epoch 9/20
875/875 [==============================] - 64s 74ms/step - loss: 0.3795 - accuracy: 0.8349
Epoch 10/20
875/875 [==============================] - 66s 75ms/step - loss: 0.302

In [26]:
max_seq_length = 50  # or any other desired sequence length
y_test_array = np.array(y_test)
if isinstance(y_test_array, tf.Tensor):
    y_test_array = y_test_array.numpy()
mlb = preprocessing.MultiLabelBinarizer()

y_test= mlb.fit_transform(y_test_array)
y_test = y_test[:,0]
X_test = tf.keras.preprocessing.sequence.pad_sequences(X_test, maxlen=max_seq_length, padding="pre", truncating="post")

model.evaluate(X_test,y_test)
model.save(r"C:\Users\Jun Liang\Documents\GitHub\NTUCClub\sentimaticModel")


875/875 [==============================] - 7s 7ms/step - loss: 0.0877 - accuracy: 0.9754
